# Part 3: Sparse matrix storage

This part is about sparse matrix storage in Numpy/Scipy. Start by running the following code cell to get some of the key modules you'll need.

In [4]:
import numpy as np
import pandas as pd
from random import sample # Used to generate a random sample
from IPython.display import display

In [5]:
import requests
import os
import hashlib
import io

## Sample data

For this part, you'll need to download the dataset below. It's a list of pairs of strings. The strings, it turns out, correspond to anonymized Yelp! user IDs; a pair $(a, b)$ exists if user $a$ is friends on Yelp! with user $b$.

**Exercise 0** (ungraded). Verify that you can obtain the dataset and take a peek by running the two code cells that follow.

In [6]:
import requests
import os
import hashlib
import io

def is_vocareum():
    return os.path.exists('.voc')

if is_vocareum():
    local_filename = '../resource/asnlib/publicdata/UserEdges-1M.csv'
else:
    local_filename = 'UserEdges-1M.csv'
    url = 'https://cse6040.gatech.edu/datasets/{}'.format(url_suffix)
    if os.path.exists(local_filename):
        print("[{}]\n==> '{}' is already available.".format(url, file))
    else:
        print("[{}] Downloading...".format(url))
        r = requests.get(url)
        with open(file, 'w', encoding=r.encoding) as f:
            f.write(r.text)
            
checksum = '4668034bbcd2fa120915ea2d15eafa8d'
with io.open(local_filename, 'r', encoding='utf-8', errors='replace') as f:
    body = f.read()
    body_checksum = hashlib.md5(body.encode('utf-8')).hexdigest()
    assert body_checksum == checksum, \
        "Downloaded file '{}' has incorrect checksum: '{}' instead of '{}'".format(local_filename,
                                                                                   body_checksum,
                                                                                   checksum)
    print("==> Checksum test passes: {}".format(checksum))
    
print("==> '{}' is ready!\n".format(local_filename))
print("(Auxiliary files appear to be ready.)")

NameError: name 'url_suffix' is not defined

In [ ]:
# Peek at the data:
edges_raw = pd.read_csv(local_filename)
display(edges_raw.head ())
print("...\n`edges_raw` has {} entries.".format(len(edges_raw)))

In [7]:
# Peek at the data:
edges_raw = pd.read_csv('./edges_raw.csv')
display(edges_raw.head ())
print("...\n`edges_raw` has {0:,d} entries.".format(len(edges_raw)))

Unnamed: 0                  Source                  Target
0           0  18kPq7GPye-YQ3LyKyAZPw  rpOyqD_893cqmDAtJLbdog
1           1  18kPq7GPye-YQ3LyKyAZPw  4U9kSBLuBDU391x6bxU-YA
2           2  18kPq7GPye-YQ3LyKyAZPw  fHtTaujcyKvXglE33Z5yIw
3           3  18kPq7GPye-YQ3LyKyAZPw  8J4IIYcqBlFch8T90N923A
4           4  18kPq7GPye-YQ3LyKyAZPw  wy6l_zUo7SN0qrvNRWgySw

...
`edges_raw` has 1,000,000 entries.


Evidently, this dataframe has one million entries.

**Exercise 1** (ungraded). Explain what the following code cell does.

In [8]:
edges_raw_trans = pd.DataFrame({'Source': edges_raw['Target'],
                                'Target': edges_raw['Source']})
print('edges_raw_trans has length {0:,d}'.format(len(edges_raw_trans)))

edges_raw_symm = pd.concat([edges_raw, edges_raw_trans])
print('edges_raw_symm has length {0:,d}'.format(len(edges_raw_symm)))

edges = edges_raw_symm.drop_duplicates(subset=(['Source', 'Target']))
print('edges has length {0:,d}'.format(len(edges)))

V_names = set(edges['Source'])
V_names.update(set(edges['Target']))

num_edges = len(edges)
num_verts = len(V_names)
print("==> |V| == {}, |E| == {}".format(num_verts, num_edges))

edges_raw_trans has length 1,000,000
edges_raw_symm has length 2,000,000


/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """


edges has length 882,640
==> |V| == 107456, |E| == 882640


**Answer.** Give this question some thought before peeking at our suggested answer, which follows.

Recall that the input dataframe, `edges_raw`, has a row $(a, b)$ if $a$ and $b$ are friends. But here is what is unclear at the outset: if $(a, b)$ is an entry in this table, is $(b, a)$ also an entry? The code in the above cell effectively figures that out, by computing a dataframe, `edges`, that contains both $(a, b)$ and $(b, a)$, with no additional duplicates, i.e., no copies of $(a, b)$.

It also uses sets to construct a set, `V_names`, that consists of all the names. Evidently, the dataset consists of 107,456 unique names and 441,320 unique pairs, or 882,640 pairs when you "symmetrize" to ensure that both $(a, b)$ and $(b, a)$ appear.

## Graphs

One way a computer scientist thinks of this collection of pairs is as a _graph_: 
https://en.wikipedia.org/wiki/Graph_(discrete_mathematics%29)

The names or user IDs are _nodes_ or _vertices_ of this graph; the pairs are _edges_, or arrows that connect vertices. That's why the final output objects are named `V_names` (for vertex names) and `edges` (for the vertex-to-vertex relationships). The process or calculation to ensure that both $(a, b)$ and $(b, a)$ are contained in `edges` is sometimes referred to as _symmetrizing_ the graph: it ensures that if an edge $a \rightarrow b$ exists, then so does $b \rightarrow a$. If that's true for all edges, then the graph is _undirected_. The Wikipedia page linked to above explains these terms with some examples and helpful pictures, so take a moment to review that material before moving on.

We'll also refer to this collection of vertices and edges as the _connectivity graph_.

## Sparse matrix storage: Baseline methods

Let's start by reminding ourselves how our previous method for storing sparse matrices, based on nested default dictionaries, works and performs.

In [9]:
def sparse_matrix(base_type=float):
    """Returns a sparse matrix using nested default dictionaries."""
    from collections import defaultdict
    return defaultdict(lambda: defaultdict (base_type))

def dense_vector(init, base_type=float):
    """
    Returns a dense vector, either of a given length
    and initialized to 0 values or using a given list
    of initial values.
    """
    # Case 1: `init` is a list of initial values for the vector entries
    if type(init) is list:
        initial_values = init
        return [base_type(x) for x in initial_values]
    
    # Else, case 2: `init` is a vector length.
    assert type(init) is int
    return [base_type(0)] * init

**Exercise 2** (3 points). Implement a function to compute $y \leftarrow A x$. Assume that the keys of the sparse matrix data structure are integers in the interval $[0, s)$ where $s$ is the number of rows or columns as appropriate.

In [10]:
test_A = sparse_matrix()
test_A

test_A[0][1] = -2.5
test_A[0][2] = 1.2
test_A[1][0] = 0.1
test_A[1][1] = 1.
test_A[2][0] = 6.
test_A[2][1] = -1.

test_A

defaultdict(<function __main__.sparse_matrix.<locals>.<lambda>()>,
            {0: defaultdict(float, {1: -2.5, 2: 1.2}),
             1: defaultdict(float, {0: 0.1, 1: 1.0}),
             2: defaultdict(float, {0: 6.0, 1: -1.0})})

In [11]:
display(test_A.get(0).keys())
display(test_A.get(0).values())

dict_keys([1, 2])

dict_values([-2.5, 1.2])

In [12]:
test_A[0][1]

-2.5

In [13]:
list(zip(test_A.get(0).keys(), test_A.get(0).values()))

[(1, -2.5), (2, 1.2)]

In [14]:
def spmv(A, x, num_rows=None): 
    if num_rows is None:
        num_rows = max(A.keys()) + 1
    y = dense_vector(num_rows) 
    
    # Recall: y = A*x is, conceptually,
    # F or all i, y[i] == sum over all j of (A[i, j] * x[j])
    
    ###
    for i in range(len(A)):
        # Gets all the indices of that row in A w/ non-zero values
        keys = A[i].keys() 
        
        # Only perform the multiplcation for non-zero values of A[i], waste of time/energy/memory otherwise
        to_sum = [(xj * A[i][j]) for j, xj in enumerate(x) if j in keys] 

        # Replace the zeros in the y above, which was assigned a dense vector of 0's
        y[i] = np.sum(to_sum) 
    ###
    
    return y

In [15]:
# Test cell: `spmv_baseline_test`

#   / 0.   -2.5   1.2 \   / 1. \   / -1.4 \
#   | 0.1   1.    0.  | * | 2. | = |  2.1 |
#   \ 6.   -1.    0.  /   \ 3. /   \  4.0 /

A = sparse_matrix ()
A[0][1] = -2.5
A[0][2] = 1.2
A[1][0] = 0.1
A[1][1] = 1.
A[2][0] = 6.
A[2][1] = -1.

x = dense_vector ([1, 2, 3])
y0 = dense_vector ([-1.4, 2.1, 4.0])


# Try your code:
y = spmv(A, x)

max_abs_residual = max([abs(a-b) for a, b in zip(y, y0)])

print ("==> A:", A)
print ("==> x:", x)
print ("==> True solution, y0:", y0)
print ("==> Your solution, y:", y)
print ("==> Residual (infinity norm):", max_abs_residual)
assert max_abs_residual <= 1e-14

print ("\n(Passed.)")

==> A: defaultdict(<function sparse_matrix.<locals>.<lambda> at 0x7f4ccb3d1488>, {0: defaultdict(<class 'float'>, {1: -2.5, 2: 1.2}), 1: defaultdict(<class 'float'>, {0: 0.1, 1: 1.0}), 2: defaultdict(<class 'float'>, {0: 6.0, 1: -1.0})})
==> x: [1.0, 2.0, 3.0]
==> True solution, y0: [-1.4, 2.1, 4.0]
==> Your solution, y: [-1.4000000000000004, 2.1000000000000001, 4.0]
==> Residual (infinity norm): 4.4408920985e-16

(Passed.)


Next, let's convert the `edges` input into a sparse matrix representing its connectivity graph. To do so, we'll first want to map names to integers.

In [16]:
id2name = {} # id2name[id] == name
name2id = {} # name2id[name] == id

for k, v in enumerate (V_names):
    # for debugging
    if k <= 5: print ("Name %s -> Vertex id %d" % (v, k))
    if k == 6: print ("...")
        
    id2name[k] = v
    name2id[v] = k

Name UR_l_tfPthGjD2SHmLGM7A -> Vertex id 0
Name ASC2vbl77V7L7I8h9md9-g -> Vertex id 1
Name QHWGKJlwpchGsEURbbSDKw -> Vertex id 2
Name zLfRCslQ2W3Dcg8_yju53A -> Vertex id 3
Name zyO-mzOo2d__c4hDxdVOYg -> Vertex id 4
Name Xdh0mp8nKs-2X90trwoDnQ -> Vertex id 5
...


In [17]:
# id2name

In [18]:
# name2id

**Exercise 3** (3 points). Given `id2name` and `name2id` as computed above, convert `edges` into a sparse matrix, `G`, where there is an entry `G[s][t] == 1.0` wherever an edge `(s, t)` exists.

**Note** - This step might take time for the kernel to process as there are 1 million rows

In [19]:
412 in edges.index

False

In [20]:
edges.index

Int64Index([     0,      1,      2,      3,      4,      5,      6,      7,
                 8,      9,
            ...
            999994, 999997, 999998, 999999, 999990, 999991, 999992, 999993,
            999994, 999997],
           dtype='int64', length=882640)

In [21]:
edges.head()

Source                  Target  Unnamed: 0
0  18kPq7GPye-YQ3LyKyAZPw  rpOyqD_893cqmDAtJLbdog         0.0
1  18kPq7GPye-YQ3LyKyAZPw  4U9kSBLuBDU391x6bxU-YA         1.0
2  18kPq7GPye-YQ3LyKyAZPw  fHtTaujcyKvXglE33Z5yIw         2.0
3  18kPq7GPye-YQ3LyKyAZPw  8J4IIYcqBlFch8T90N923A         3.0
4  18kPq7GPye-YQ3LyKyAZPw  wy6l_zUo7SN0qrvNRWgySw         4.0

In [22]:
G = sparse_matrix()

###

# Make a copy of the edges DataFrame and reset the index
# edges as it is right now does not have ordered indices
edges_copy = edges.copy()
edges_copy.reset_index(drop=True, inplace=True)

for i in range(len(edges_copy)):
    
    # get the corresponding Source and corresponding Target
    s = edges_copy.loc[i, 'Source']
    t = edges_copy.loc[i, 'Target']
    
    # have to get the id's in order to assign as keys for G (sparse matrix)
    s_id = name2id[s]
    t_id = name2id[t]
    
    G[s_id][t_id] = 1.0
###

In [23]:
type(G)

collections.defaultdict

In [24]:
# Test cell: `edges2spmat1_test`

G_rows_nnz = [len(row_i) for row_i in G.values()]
print ("G has {} vertices and {} edges.".format(len(G.keys()), sum(G_rows_nnz)))

assert len(G.keys()) == num_verts
assert sum(G_rows_nnz) == num_edges

# Check a random sample
for k in sample(range(num_edges), 1000):
    i = name2id[edges['Source'].iloc[k]]
    j = name2id[edges['Target'].iloc[k]]
    assert i in G
    assert j in G[i]
    assert G[i][j] == 1.0

print ("\n(Passed.)")

G has 107456 vertices and 882640 edges.

(Passed.)


**Exercise 4** (3 points). In the above, we asked you to construct `G` using integer keys. However, since we are, after all, using default dictionaries, we could also use the vertex _names_ as keys. Construct a new sparse matrix, `H`, which uses the vertex names as keys instead of integers.

In [25]:
H = sparse_matrix()

###
for i in range(len(edges_copy)):

    # get the names from the edges_copy table
    s = edges_copy.loc[i, 'Source']
    t = edges_copy.loc[i, 'Target']
    
    H[s][t] = 1.0
###

In [26]:
# Test cell: `create_H_test`

H_rows_nnz = [len(h) for h in H.values()]
print("`H` has {} vertices and {} edges.".format(len(H.keys()), sum(H_rows_nnz)))

assert len(H.keys()) == num_verts
assert sum(H_rows_nnz) == num_edges

# Check a random sample
for i in sample(G.keys(), 100):
    i_name = id2name[i]
    assert i_name in H
    assert len(G[i]) == len(H[i_name])
    
print ("\n(Passed.)")

`H` has 107456 vertices and 882640 edges.

(Passed.)


**Exercise 5** (3 points). Implement a sparse matrix-vector multiply for matrices with named keys. In this case, it will be convenient to have vectors that also have named keys; assume we use dictionaries to hold these vectors as suggested in the code skeleton, below.

**Hint** - To help you understand more about the exercise, go back to **Exercise 2** and see what we did there. There is only one technical change between Ex2 and Ex5

In [27]:
H

defaultdict(<function __main__.sparse_matrix.<locals>.<lambda>()>,
            {'18kPq7GPye-YQ3LyKyAZPw': defaultdict(float,
                         {'rpOyqD_893cqmDAtJLbdog': 1.0,
                          '4U9kSBLuBDU391x6bxU-YA': 1.0,
                          'fHtTaujcyKvXglE33Z5yIw': 1.0,
                          '8J4IIYcqBlFch8T90N923A': 1.0,
                          'wy6l_zUo7SN0qrvNRWgySw': 1.0,
                          'HDQixQ-WZEV0LVPJlIGQeQ': 1.0,
                          'T4kuUr_iJiywOPdyM7gTHQ': 1.0,
                          'z_5D4XEIlGAPjG3Os9ix5A': 1.0,
                          'i63u3SdbrLsP4FxiSKP0Zw': 1.0,
                          'pnrGw4ciBXJ6U5QB2m0F5g': 1.0,
                          'ytjCBxosVSqCOQ62c4KAxg': 1.0,
                          'r5uiIxwJ-I-oHBkNY2Ha3Q': 1.0,
                          'niWoSKswEbooJC_M7HMbGw': 1.0,
                          'kwoxiKMyoYjB1wTCYAjYRg': 1.0,
                          '9A8OuP6XwLwnNb9ov3_Ncw': 1.0,
                    

In [28]:
# Exercise 2 (for reference)
def spmv(A, x, num_rows=None): 
    if num_rows is None:
        num_rows = max(A.keys()) + 1
    y = dense_vector(num_rows) 
    
    # Recall: y = A*x is, conceptually,
    # F or all i, y[i] == sum over all j of (A[i, j] * x[j])
    
    ###
    for i in range(len(A)):
        # Gets all the indices of that row in A w/ non-zero values
        keys = A[i].keys() 
        
        # Only perform the multiplcation for non-zero values of A[i], waste of time/energy/memory otherwise
        to_sum = [(xj * A[i][j]) for j, xj in enumerate(x) if j in keys] 

        # Replace the zeros in the y above, which was assigned a dense vector of 0's
        y[i] = np.sum(to_sum) 
    ###
    
    return y

In [29]:
len(H)

107456

In [30]:
# H.keys()

In [31]:
def vector_keyed(keys=None, values=0, base_type=float):
    if keys is not None:
        if type(values) is not list:
            values = [base_type(values)] * len(keys)
        else:
            values = [base_type(v) for v in values]
        x = dict(zip(keys, values))
    else:
        x = {}
    return x

def spmv_keyed(A, x):
    """Performs a sparse matrix-vector multiply for keyed matrices and vectors."""
    assert type(x) is dict
    
    # this is the output vector, need to update this dict with each key
    y = vector_keyed(keys=A.keys(), values=0.0)
    
    ###
    # Iterate over the first layer of keys in A
    row = A.keys()
    
    # For each of the rows, find the keys in there
    for key in row:
        y[key] = np.sum([A[key][k] * x_keyed[k] for k in A[key] if k in x_keyed.keys()])
    ###
    
    return y

In [32]:
# [key for key in A_keyed.keys()]

In [33]:
# [val for val in A_keyed.values()]

In [34]:
# row = A_keyed.keys()

In [35]:
# for key in row:
#     print(A_keyed[key].keys())

In [36]:
# for key in row:
#     print([A_keyed[key][k] * x_keyed[k] for k in A_keyed[key] if k in x_keyed.keys()])

In [37]:
# Test cell: `spmv_keyed_test`

#   'row':  / 0.   -2.5   1.2 \   / 1. \   / -1.4 \
#  'your':  | 0.1   1.    0.  | * | 2. | = |  2.1 |
#  'boat':  \ 6.   -1.    0.  /   \ 3. /   \  4.0 /

KEYS = ['row', 'your', 'boat']

A_keyed = sparse_matrix ()
A_keyed['row']['your'] = -2.5
A_keyed['row']['boat'] = 1.2
A_keyed['your']['row'] = 0.1
A_keyed['your']['your'] = 1.
A_keyed['boat']['row'] = 6.
A_keyed['boat']['your'] = -1.

x_keyed = vector_keyed (KEYS, [1, 2, 3])
y0_keyed = vector_keyed (KEYS, [-1.4, 2.1, 4.0])


# Try your code:
y_keyed = spmv_keyed (A_keyed, x_keyed)

# Measure the residual:
residuals = [(y_keyed[k] - y0_keyed[k]) for k in KEYS]
max_abs_residual = max ([abs (r) for r in residuals])

print ("==> A_keyed:", A_keyed)
print ("==> x_keyed:", x_keyed)
print ("==> True solution, y0_keyed:", y0_keyed)
print ("==> Your solution:", y_keyed)
print ("==> Residual (infinity norm):", max_abs_residual)
assert max_abs_residual <= 1e-14

print ("\n(Passed.)")

==> A_keyed: defaultdict(<function sparse_matrix.<locals>.<lambda> at 0x7f4cc054b730>, {'row': defaultdict(<class 'float'>, {'your': -2.5, 'boat': 1.2}), 'your': defaultdict(<class 'float'>, {'row': 0.1, 'your': 1.0}), 'boat': defaultdict(<class 'float'>, {'row': 6.0, 'your': -1.0})})
==> x_keyed: {'row': 1.0, 'your': 2.0, 'boat': 3.0}
==> True solution, y0_keyed: {'row': -1.4, 'your': 2.1, 'boat': 4.0}
==> Your solution: {'row': -1.4000000000000004, 'your': 2.1000000000000001, 'boat': 4.0}
==> Residual (infinity norm): 4.4408920985e-16

(Passed.)


Let's benchmark `spmv()` against `spmv_keyed()` on the full data set. Do they perform differently?

In [38]:
# x = dense_vector ([1.] * num_verts)
# %timeit spmv (G, x)

# x_keyed = vector_keyed (keys=[v for v in V_names], values=1.)
# %timeit spmv_keyed (H, x_keyed)

## Alternative formats: 

Take a look at the following slides: [link](https://www.dropbox.com/s/4fwq21dy60g4w4u/cse6040-matrix-storage-notes.pdf?dl=0). These slides cover the basics of two list-based sparse matrix formats known as _coordinate format_ (COO) and _compressed sparse row_ (CSR). We will also discuss them briefly below.

### Coordinate Format (COO)
In this format we store three lists, one each for rows, columns and the elements of the matrix. Look at the below picture to understand how these lists are formed.

![Coordinate (COO) storage](https://github.com/cse6040/labs-fa17/raw/master/lab10-numpy/coo.png)

**Exercise 6** (3 points). Convert the `edges[:]` data into a coordinate (COO) data structure in native Python using three lists, `coo_rows[:]`, `coo_cols[:]`, and `coo_vals[:]`, to store the row indices, column indices, and matrix values, respectively. Use integer indices and set all values to 1.

**Hint** - Think of what rows, columns and values mean conceptually when you relate it with our dataset of edges

In [39]:
###
coo_rows = [name2id[s] for s in edges['Source']]
coo_cols = [name2id[t] for t in edges['Target']]
coo_vals = [1.0] * len(edges)
###

In [40]:
# Test cell: `create_coo_test`

assert len (coo_rows) == num_edges
assert len (coo_cols) == num_edges
assert len (coo_vals) == num_edges
assert all ([v == 1. for v in coo_vals])

# Randomly check a bunch of values
coo_zip = zip (coo_rows, coo_cols, coo_vals)
for i, j, a_ij in sample (list (coo_zip), 1000):
    assert (i in G) and j in G[i]
    
print ("\n(Passed.)")


(Passed.)


**Exercise 7** (3 points). Implement a sparse matrix-vector multiply routine for COO implementation.

In [41]:
test_A_coo_rows = [0, 0, 1, 1, 2, 2]
test_A_coo_cols = [1, 2, 0, 1, 0, 1]
test_A_coo_vals = [-2.5, 1.2, 0.1, 1., 6., -1.]

test_x = dense_vector([1, 2, 3])
test_y0 = dense_vector([-1.4, 2.1, 4.0])

In [42]:
test_x

[1.0, 2.0, 3.0]

In [43]:
test_y0

[-1.4, 2.1, 4.0]

In [44]:
def spmv_coo(R:list, C:list, V:list, x:list, num_rows=None):
    """
    Returns y = A*x, where A has 'm' rows and is stored in
    COO format by the array triples, (R, C, V).
    """
#     assert type(x) is list
#     assert type(R) is list
#     assert type(C) is list
#     assert type(V) is list
    assert len(R) == len(C) == len(V)
    if num_rows is None:
        num_rows = max(R) + 1
    
    y = dense_vector(num_rows)
    
    ###
    matrix_rcv = zip(R, C, V)
    
    for i, j, aij in matrix_rcv:
        y[i] += (aij * x[j])
    ###
    
    return y

In [45]:
# Test cell: `spmv_coo_test`

#   / 0.   -2.5   1.2 \   / 1. \   / -1.4 \
#   | 0.1   1.    0.  | * | 2. | = |  2.1 |
#   \ 6.   -1.    0.  /   \ 3. /   \  4.0 /

A_coo_rows = [0, 0, 1, 1, 2, 2]
A_coo_cols = [1, 2, 0, 1, 0, 1]
A_coo_vals = [-2.5, 1.2, 0.1, 1., 6., -1.]

x = dense_vector([1, 2, 3])
y0 = dense_vector([-1.4, 2.1, 4.0])

# Try your code:
y_coo = spmv_coo(A_coo_rows, A_coo_cols, A_coo_vals, x)

max_abs_residual = max ([abs(a-b) for a, b in zip(y_coo, y0)])

print("==> A_coo:", list(zip(A_coo_rows, A_coo_cols, A_coo_vals)))
print("==> x:", x)
print("==> True solution, y0:", y0)
print("==> Your solution:", y_coo)
print("==> Residual (infinity norm):", max_abs_residual)
assert max_abs_residual <= 1e-15

print("\n(Passed.)")

==> A_coo: [(0, 1, -2.5), (0, 2, 1.2), (1, 0, 0.1), (1, 1, 1.0), (2, 0, 6.0), (2, 1, -1.0)]
==> x: [1.0, 2.0, 3.0]
==> True solution, y0: [-1.4, 2.1, 4.0]
==> Your solution: [-1.4000000000000004, 2.1, 4.0]
==> Residual (infinity norm): 4.440892098500626e-16

(Passed.)


Let's see how fast this is...

In [46]:
x = dense_vector([1.] * num_verts)
%timeit spmv_coo(coo_rows, coo_cols, coo_vals, x)

273 ms ± 36.7 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


### Compressed Sparse Row Format
This is similar to the COO format excpet that it is much more compact and takes up less storage. Look at the picture below to understand more about this representation

![Compressed sparse row (CSR) format](https://github.com/cse6040/labs-fa17/raw/master/lab10-numpy/csr.png)

**Exercise 8** (3 points). Now create a CSR data structure, again using native Python lists. Name your output CSR lists `csr_ptrs`, `csr_inds`, and `csr_vals`.

It's easiest to start with the COO representation. We've given you some starter code. Unlike most of the exercises, instead of creating a function, you have to compute csr_ptrs here

In [47]:
docs = [["hello", "world", "hello"], ["goodbye", "cruel", "world"]]

# always start w/ 0 for indptr
indptr = [0] # csrptr equivalent
indices = [] # colinds equivalent
data = []    # values equiavlent
vocabulary = {}

for d in docs:
    for term in d:
        # if term is in the dictionary 'vocabulary', assign it the value
        # if the term is not a key in the ditionary 'vocabulary', pass it the default of
        # its length
        index = vocabulary.setdefault(term, len(vocabulary))
        indices.append(index)
        data.append(1)
        
    print('Indices in this loop:', indices)
    print('Length of indices in this loop:', len(indices))
    
    indptr.append(len(indices))
    print('Updated index pointer:', indptr)
    print('\n')

Indices in this loop: [0, 1, 0]
Length of indices in this loop: 3
Updated index pointer: [0, 3]


Indices in this loop: [0, 1, 0, 2, 3, 1]
Length of indices in this loop: 6
Updated index pointer: [0, 3, 6]




In [48]:
from operator import itemgetter

myA = sorted(zip(coo_rows, coo_cols, coo_vals), key=itemgetter(0))
myA_df = pd.DataFrame(myA, columns=['rowind', 'colind', 'value'])
myA_groupbysum = myA_df.groupby('rowind').sum()

In [49]:
myind_ptrs = [0]

for i in range(len(myA_groupbysum)):
    myind_ptrs.append(int(myA_groupbysum.loc[i, 'value']))

In [50]:
pd.DataFrame(myA[:10], columns=['rowind', 'colind', 'value'])

rowind  colind  value
0       0   40854    1.0
1       1   19521    1.0
2       2   66101    1.0
3       2  107221    1.0
4       2   43451    1.0
5       2   65649    1.0
6       2   48288    1.0
7       2   57423    1.0
8       3   86353    1.0
9       3    7911    1.0

In [51]:
myrow_ptrs = (np.cumsum(myind_ptrs))
myrow_ptrs

array([     0,      1,      2, ..., 882632, 882633, 882640])

In [52]:
from operator import itemgetter
C = sorted(zip(coo_rows, coo_cols, coo_vals), key=itemgetter(0))
nnz = len(C)
assert nnz >= 1

assert (C[-1][0] + 1) == num_verts  # Why?

csr_inds = [j for _, j, _ in C]
csr_vals = [a_ij for _, _, a_ij in C]

# Your task: Compute `csr_ptrs`
###
C_df = pd.DataFrame(C, columns=['rowinds', 'colinds', 'values'])
C_groupbysum_df = C_df.groupby('rowinds').sum()

ptrs = [0]
for i in range(len(C_groupbysum_df)):
    ptrs.append(int(C_groupbysum_df.loc[i, 'values']))
###
csr_ptrs = list(np.cumsum(ptrs))

In [53]:
# Test cell: `create_csr_test`

assert type(csr_ptrs) is list, "`csr_ptrs` is not a list."
assert type(csr_inds) is list, "`csr_inds` is not a list."
assert type(csr_vals) is list, "`csr_vals` is not a list."

assert len(csr_ptrs) == (num_verts + 1), "`csr_ptrs` has {} values instead of {}".format(len(csr_ptrs), num_verts+1)
assert len(csr_inds) == num_edges, "`csr_inds` has {} values instead of {}".format(len(csr_inds), num_edges)
assert len(csr_vals) == num_edges, "`csr_vals` has {} values instead of {}".format(len(csr_vals), num_edges)
assert csr_ptrs[num_verts] == num_edges, "`csr_ptrs[{}]` == {} instead of {}".format(num_verts, csr_ptrs[num_verts], num_edges)

# Check some random entries
for i in sample(range(num_verts), 10000):
    assert i in G
    a, b = csr_ptrs[i], csr_ptrs[i+1]
    msg_prefix = "Row {} should have these nonzeros: {}".format(i, G[i])
    assert (b-a) == len(G[i]), "{}, which is {} nonzeros; instead, it has just {}.".format(msg_prefix, len(G[i]), b-a)
    assert all([(j in G[i]) for j in csr_inds[a:b]]), "{}. However, it may have missing or incorrect column indices: csr_inds[{}:{}] == {}".format(msg_prefix, a, b, csr_inds[a:b])
    assert all([(j in csr_inds[a:b] for j in G[i].keys())]), "{}. However, it may have missing or incorrect column indices: csr_inds[{}:{}] == {}".format(msg_prefix, a, b, csr_inds[a:b])

print ("\n(Passed.)")


(Passed.)


**Exercise 9** (3 points). Now implement a CSR-based sparse matrix-vector multiply.

In [54]:
myrow_ptrs = (np.cumsum(myind_ptrs))
myrow_ptrs

array([     0,      1,      2, ..., 882632, 882633, 882640])

In [55]:
numcols = [0]
for i, integer in enumerate(myrow_ptrs):
    if i > 0:
        numcols.append(integer - myrow_ptrs[i-1])

display(len(numcols))    
display(numcols[:10])    
display(numcols[-10:])

# numcols is basically representing how many values are in a column that are non-zero
# before moving onto the next row that has non-zero values

107457

[0, 1, 1, 6, 3, 2, 3, 5, 1, 6]

[1, 1, 3, 4, 1, 7, 1, 1, 1, 7]

In [ ]:
# using numcols, that's how many values to grab before jumping to the next row
y = dense_vector(len(myrow_ptrs))

In [58]:
my_A_csr_ptrs = [ 0,        2,       4,       6]
my_A_csr_cols = [ 1,   2,   0,   1,  0,   1]
my_A_csr_vals = [-2.5, 1.2, 0.1, 1., 6., -1.]

my_x = dense_vector([1, 2, 3])
my_y0 = dense_vector([-1.4, 2.1, 4.0])

In [64]:
# nonzero_colvals
nonzero_colvals = [0]
for i, integer in enumerate(my_A_csr_ptrs):
    if i > 0:
        nonzero_colvals.append(integer - my_A_csr_ptrs[i-1])

display(len(nonzero_colvals))    
display(nonzero_colvals[:3])    
display(nonzero_colvals[-3:])
display(nonzero_colvals)

4

[0, 2, 2]

[2, 2, 2]

[0, 2, 2, 2]

In [76]:
# these are indices I want to slice by in my csr_cols and csr_vals
for ptr in zip(my_A_csr_ptrs[:-1], my_A_csr_ptrs[1:]):
    print(ptr)

(0, 2)
(2, 4)
(4, 6)


In [85]:
# now get the applicable column indices and values for that particular rowe we're on
for indices in zip(my_A_csr_ptrs[:-1], my_A_csr_ptrs[1:]):
    colinds = my_A_csr_cols[indices[0]:indices[1]]
    vals = my_A_csr_vals[indices[0]:indices[1]]
    print('The column index slice is: ', colinds)
    print('The value slide is: ', vals)

The column index slice is:  [1, 2]
The value slide is:  [-2.5, 1.2]
The column index slice is:  [0, 1]
The value slide is:  [0.1, 1.0]
The column index slice is:  [0, 1]
The value slide is:  [6.0, -1.0]


In [90]:
def spmv_csr(ptr:list, ind:list, val:list, x:list, num_rows=None):

    if num_rows is None: num_rows = len(ptr) - 1
    assert len(ptr) >= (num_rows+1)  # Why? 
    assert len(ind) >= ptr[num_rows]  # Why? 
    assert len(val) >= ptr[num_rows]  # Why? 
    
    # y is my output vector
    y = dense_vector(num_rows)
    
    ###
    to_sum = []
    for indices in zip(ptr[:-1], ptr[1:]):
        colinds = ind[indices[0]:indices[1]]
        vals = val[indices[0]:indices[1]]
#         print('The column index slice is: ', colinds)
#         print('The value slide is: ', vals)
        
        # now go into the x vector and get the corresponding values
        to_sum.append([(x[ind] * vals[i]) for i, ind in enumerate(colinds)])
        
    for i in range(len(y)):
        y[i] = np.sum(to_sum[i])
    ###
    
    return y

In [91]:
# Test cell: `spmv_csr_test`

#   / 0.   -2.5   1.2 \   / 1. \   / -1.4 \
#   | 0.1   1.    0.  | * | 2. | = |  2.1 |
#   \ 6.   -1.    0.  /   \ 3. /   \  4.0 /

A_csr_ptrs = [ 0,        2,       4,       6]
A_csr_cols = [ 1,   2,   0,   1,  0,   1]
A_csr_vals = [-2.5, 1.2, 0.1, 1., 6., -1.]

x = dense_vector([1, 2, 3])
y0 = dense_vector([-1.4, 2.1, 4.0])

# Try your code:
y_csr = spmv_csr(A_csr_ptrs, A_csr_cols, A_csr_vals, x)

max_abs_residual = max([abs(a-b) for a, b in zip(y_csr, y0)])

print ("==> A_csr_ptrs:", A_csr_ptrs)
print ("==> A_csr_{cols, vals}:", list(zip(A_csr_cols, A_csr_vals)))
print ("==> x:", x)
print ("==> True solution, y0:", y0)
print ("==> Your solution:", y_csr)
print ("==> Residual (infinity norm):", max_abs_residual)
assert max_abs_residual <= 1e-14

print ("\n(Passed.)")

==> A_csr_ptrs: [0, 2, 4, 6]
==> A_csr_{cols, vals}: [(1, -2.5), (2, 1.2), (0, 0.1), (1, 1.0), (0, 6.0), (1, -1.0)]
==> x: [1.0, 2.0, 3.0]
==> True solution, y0: [-1.4, 2.1, 4.0]
==> Your solution: [-1.4000000000000004, 2.1000000000000001, 4.0]
==> Residual (infinity norm): 4.4408920985e-16

(Passed.)


In [92]:
x = dense_vector([1.] * num_verts)
%timeit spmv_csr(csr_ptrs, csr_inds, csr_vals, x)

1.18 s ± 105 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


## Using Scipy's implementations

What you should have noticed is that the list-based COO and CSR formats do not really lead to sparse matrix-vector multiply implementations that are much faster than the dictionary-based methods. Let's instead try Scipy's native COO and CSR implementations.

In [93]:
import numpy as np
import scipy.sparse as sp

A_coo_sp = sp.coo_matrix((coo_vals, (coo_rows, coo_cols)))
A_csr_sp = A_coo_sp.tocsr() # Alternatively: sp.csr_matrix((val, ind, ptr))
x_sp = np.ones(num_verts)

print ("\n==> COO in Scipy:")
%timeit A_coo_sp.dot (x_sp)

print ("\n==> CSR in Scipy:")
%timeit A_csr_sp.dot (x_sp)


==> COO in Scipy:
3.29 ms ± 475 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)

==> CSR in Scipy:
2.15 ms ± 181 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


**Fin!** If your notebook runs to this point without error, try submitting it.